# Using ChatGPT to analyze hotel reviews
(c) Nuno Antonio 2023-2025<br>
Version 1.10 - 2025-05-02

### Import packages
If required, install packages using "!pip install <package name>"

In [1]:
import numpy as np
import pandas as pd
import requests
from tqdm import tqdm
import time
import ydata_profiling as ydp
import json
import ast

In [2]:
import openai                           # Documentation: https://github.com/openai/openai-python
import tiktoken                         # Documentation: https://github.com/openai/tiktoken
from skllm.config import SKLLMConfig    # !pip install scikit-llm

### OpenAI Setup

In [31]:
# OpenAI API key
openai.api_key = "REPLACE THIS TEXT WITH YOUR KEY"

SKLLMConfig.set_openai_key(openai.api_key)

In [4]:
# OpenAI API URL
GPT_API_URL = "https://api.openai.com/v1/chat/completions"

In [5]:
# Check if API key is valid
def check_openai_api_key():
    try:
        openai.models.list()
    except openai.AuthenticationError as e:
        return False
    else:
        return True

is_valid = check_openai_api_key()
if is_valid:
    print("Valid OpenAI API key")
else:
    print("Invalid OpenAI API key")

Valid OpenAI API key


### OpenAI usage

Online can be checked at https://platform.openai.com/usage

In [6]:
# API headers
headers = {'Authorization': f'Bearer {openai.api_key}'}

# API endpoint
url = 'https://api.openai.com/v1/usage'

# Date for which to get usage data
params = {'date': '2025-05-01'}

# Send API request and get response
response = requests.get(url, headers=headers, params=params)

print(response.json())

{'object': 'list', 'data': [], 'ft_data': [], 'dalle_api_data': [], 'whisper_api_data': [], 'tts_api_data': [], 'assistant_code_interpreter_data': [], 'retrieval_storage_data': []}


### Tokens counting

To count tokens online use: https://platform.openai.com/tokenizer


In [7]:
# Function to count tokens
def num_tokens_from_string(string: str, encoding_name: str) -> int:
    """Returns the number of tokens in a text string."""
    encoding = tiktoken.get_encoding(encoding_name)
    num_tokens = len(encoding.encode(string))
    return num_tokens 

# Example
num_tokens_from_string("The ministry of silly walks", "cl100k_base")

5

In [8]:
def compare_encodings(example_string: str) -> None:
    """Prints a comparison of three string encodings."""
    # print the example string
    print(f'\nExample string: "{example_string}"')
    # for each encoding, print the # of tokens, the token integers, and the token bytes
    for encoding_name in ["r50k_base", "p50k_base", "cl100k_base"]:
        encoding = tiktoken.get_encoding(encoding_name)
        token_integers = encoding.encode(example_string)
        num_tokens = len(token_integers)
        token_bytes = [encoding.decode_single_token_bytes(token) for token in token_integers]
        print()
        print(f"{encoding_name}: {num_tokens} tokens")
        print(f"token integers: {token_integers}")
        print(f"token bytes: {token_bytes}")
        
# Example
compare_encodings("Monty Python's The Ministry of Silly Walks")


Example string: "Monty Python's The Ministry of Silly Walks"

r50k_base: 11 tokens
token integers: [26031, 88, 11361, 338, 383, 9475, 286, 311, 6548, 6445, 591]
token bytes: [b'Mont', b'y', b' Python', b"'s", b' The', b' Ministry', b' of', b' S', b'illy', b' Wal', b'ks']

p50k_base: 11 tokens
token integers: [26031, 88, 11361, 338, 383, 9475, 286, 311, 6548, 6445, 591]
token bytes: [b'Mont', b'y', b' Python', b"'s", b' The', b' Ministry', b' of', b' S', b'illy', b' Wal', b'ks']

cl100k_base: 11 tokens
token integers: [35515, 88, 13325, 596, 578, 20214, 315, 8211, 398, 12839, 82]
token bytes: [b'Mont', b'y', b' Python', b"'s", b' The', b' Ministry', b' of', b' Sil', b'ly', b' Walk', b's']


### Load data

In [9]:
# Load dataset
ds = pd.read_excel("HotelsAlgarve2019.xlsx")

### Data understanding

In [10]:
# Describe
ds.describe(include='all').T

count unique  \
HotelID                  17814.0    NaN   
Language                   17814      6   
GlobalRating             17814.0    NaN   
TotalReviewOnSite        17814.0    NaN   
ExtractedReviews         17814.0    NaN   
PositionInRegionRanking  17814.0    NaN   
SitesInRegionRanking     17814.0    NaN   
TripadvisorReviewID      17814.0    NaN   
ReviewRating             17814.0    NaN   
PublishedDate              17814     12   
Name                       17813  16203   
Location                   12434   4263   
TotalContributions       17487.0    NaN   
FullText                   17813  17813   

                                                                       top  \
HotelID                                                                NaN   
Language                                                           English   
GlobalRating                                                           NaN   
TotalReviewOnSite                                                      NaN   
ExtractedReviews                                                       NaN   
PositionInRegionRanking                                                NaN   
SitesInRegionRanking                                                   NaN   
TripadvisorReviewID                                                    NaN   
ReviewRating                                                           NaN   
PublishedDate                                      2019-08-01 00:00:00.000   
Name                                                                 Sarah   
Location                                            london, united kingdom   
TotalContributions                                                     NaN   
FullText                 Very good clean hotel. Excellent helpful and f...   

                          freq              mean              std         min  \
HotelID                    NaN         40.731391        37.557297         1.0   
Language                 10744               NaN              NaN         NaN   
GlobalRating               NaN          4.186567         0.417821         2.0   
TotalReviewOnSite          NaN       2085.740036      1516.716905         9.0   
ExtractedReviews           NaN        173.839901       198.799038         1.0   
PositionInRegionRanking    NaN         15.514708        22.631497         0.0   
SitesInRegionRanking       NaN         67.521107        60.573737         0.0   
TripadvisorReviewID        NaN  680555525.995004  39073160.812104  17695721.0   
ReviewRating               NaN          4.178792         1.070667         1.0   
PublishedDate             2261               NaN              NaN         NaN   
Name                         9               NaN              NaN         NaN   
Location                   517               NaN              NaN         NaN   
TotalContributions         NaN         59.615085       274.797226         1.0   
FullText                     1               NaN              NaN         NaN   

                                  25%          50%          75%          max  
HotelID                          10.0         29.0         61.0        161.0  
Language                          NaN          NaN          NaN          NaN  
GlobalRating                      4.0          4.0          4.5          5.0  
TotalReviewOnSite               863.0       1632.0       3157.0       6361.0  
ExtractedReviews                 35.0         90.0        235.0        740.0  
PositionInRegionRanking           4.0          7.0         17.0        152.0  
SitesInRegionRanking             17.0         37.0        154.0        154.0  
TripadvisorReviewID      666456189.25  684433245.0  705523729.0  751120809.0  
ReviewRating                      4.0          5.0          5.0          5.0  
PublishedDate                     NaN          NaN          NaN          NaN  
Name                              NaN          NaN          NaN          NaN  
Location                          NaN         

In [11]:
# Create a profile report
report = ydp.ProfileReport(ds)

# Show the report
report.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

100%|██████████| 14/14 [00:02<00:00,  5.80it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

### Get a sample of the data
Due to the rate limits of the free account and the amount to spend

In [12]:
# Calculate the number of samples per language based on the proportion in the dataframe
proportions = ds['Language'].value_counts(normalize=True)

# Get a stratified sample of 50 observations
sample_size = 50
stratified_sample = ds.groupby('Language', group_keys=False).apply(
    lambda x: x.sample(int(proportions[x.name] * sample_size), random_state=123)
)

# To extract exactly 50 samples
if len(stratified_sample) > sample_size:
    # Remove excess samples
    stratified_sample = stratified_sample.groupby('Language').head(
        lambda x: int(proportions[x.name] * sample_size)).reset_index(drop=True)
elif len(stratified_sample) < sample_size:
    # Add missing samples by sampling from the largest group
    additional_samples = ds[ds['Language'] == stratified_sample['Language'].value_counts().idxmax()].sample(
        sample_size - len(stratified_sample))
    stratified_sample = pd.concat([stratified_sample, additional_samples], ignore_index=True)

/var/folders/3q/yw7kv53d5mlb0smm2tg9nkgr0000gn/T/ipykernel_17538/3755382197.py:6: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  stratified_sample = ds.groupby('Language', group_keys=False).apply(


### Sentiment analysis

In [13]:
def analyze_review(review, model="gpt-3.5-turbo"):
    """ Get the sentiment of a review """
    retries = 3
    sentiment = None

    while retries > 0:
        messages = [
            {"role": "system", "content": "You are an AI language model trained to analyze and detect the sentiment of hotel reviews."},
            {"role": "user", "content": f"Analyze the following hotel review and determine if the sentiment is: positive, negative or neutral. Return only a single word, either POSITIVE, NEGATIVE or NEUTRAL: {review}"}
        ]

        completion = openai.chat.completions.create(
            model=model,
            messages=messages,
            max_tokens=3,           # Limit the number of tokens in the output
            n=1,                    # Number of outputs
            stop=None,
            temperature=0           # Measure of entropy (temperature = 0 is more factual, temperature = 1 higher degree of creativity) 
        )

        response_text = completion.choices[0].message.content
        print(response_text)
        if response_text in ["POSITIVE", "NEGATIVE", "NEUTRAL"]:
            sentiment = response_text
            break
        else:
            retries -= 1
            time.sleep(1)
    else:
        sentiment = "NEUTRAL"

    # add a delay of 4 seconds between requests to avoid hitting the free tier API call rate limit
    time.sleep(4)

    return sentiment

In [14]:
# Analyze the reviews and store the results
sentiments = []

for review in tqdm(stratified_sample["FullText"], desc="Processing reviews"):
    sentiment = analyze_review(review)
    sentiments.append(sentiment)

stratified_sample["Sentiment"] = sentiments

# Save the results to a new Excel file
output_file = "AnalyzedReviews.xlsx"
stratified_sample.to_excel(output_file, index=False)

Processing reviews:   0%|          | 0/50 [00:00<?, ?it/s]

NEGATIVE


Processing reviews:   2%|▏         | 1/50 [00:04<03:40,  4.50s/it]

POSITIVE


Processing reviews:   4%|▍         | 2/50 [00:08<03:35,  4.48s/it]

...

Processing reviews:  96%|█████████▌| 48/50 [03:38<00:08,  4.50s/it]

POSITIVE


Processing reviews:  98%|█████████▊| 49/50 [03:42<00:04,  4.47s/it]

POSITIVE


Processing reviews: 100%|██████████| 50/50 [03:47<00:00,  4.55s/it]


In [15]:
# Let's analyze some examples
stratified_sample[['FullText','Sentiment']].head(10)

FullText Sentiment
0  This is in no way a 4 star hotel ,you have to ...  NEGATIVE
1  We've just returned from a fab time at this ho...  POSITIVE
2  A warm welcome awaited us on our arrival and w...  POSITIVE
3  The place was recommended to us a high quality...  NEGATIVE
4  We booked this hotel with Jet2 holidays for a ...   NEUTRAL
5  The recent renovation of the hotel has been do...  POSITIVE
6  We have never been to Portugal before and deci...  NEGATIVE
7  Stayed at the Baia Grande with my 5 year old d...  POSITIVE
8  The Hotel da Rocha ticks all the boxes. Situat...  POSITIVE
9  Great hotel. Great staff. Even if you don't go...  POSITIVE

In [ ]:
# Check the text of a negative review
stratified_sample['FullText'].iloc[0]

'This is in no way a 4 star hotel ,you have to pay for a safe ,there is no tea or coffee making facilities in the room ,we had a dirty shower curtain not a shower screen,a plug that didn’t fit in the bath .The food is poor and not much choice but better at lunchtime than in the evening.There is absolutely nowhere nice to sit and have a drink .During the two weeks we were there the courtesy bus only ran once ,a very disappointing stay .'

In [ ]:
# Check the text of a positive review
stratified_sample['FullText'].iloc[5]

'The place was recommended to us a high quality family resort but we were very disappointed by the quality of housing, food and cleanliness overall. <br>The staff was very helpful and friendly which was the best part and helped us find outside activities which made the vacation bearable.'

### Understanding PROS and CONS

This function code will read in approximately 1,650 words (~75% of 2200 tokens) at a time and determine the pros and cons users have mentioned from that block of text.<br>
The code will then move onto the next block of 1,800 words and extract the pros and cons from it, repeating as necessary until all of the reviews have been processed.<br>
This process is necessary because of the limits on how much input text chatGPT 3.5 can handle at one time. 

The model can be changed to gpt-4o-mini, allowing the context to be 200,000 tokens. If you want, you can try the block_size and the model name.  

In [18]:
def generate_proscons_list(text):
    word_blocks = text.split(' ')
    block_size = 2200
    blocks = [' '.join(word_blocks[i:i + block_size]) for i in range(0, len(word_blocks), block_size)]

    proscons = []

    for block in tqdm(blocks, desc="Processing blocks", unit="block"):
        messages = [
            {"role": "system", "content": "You are an AI language model trained to create a list of the most common pros and cons for hotel users based on online review summaries."},
            {"role": "user", "content": f"Based on the following hotel review summaries, create a list, in English, of the most common pros and cons for the hotels: {block}"}
        ]

        completion = openai.chat.completions.create(
            model="gpt-3.5-turbo",
            messages=messages,
            max_tokens=300,             # limits the output size to 300 tokens
            n=1,
            stop=None,
            temperature=0.5             # limit the "creativity"
        )

        procon = completion.choices[0].message.content
        proscons.append(procon)

    # Combine the pros and cons that chatGPT found into a list 
    combined_proscons = "\n\n".join(proscons)
    return combined_proscons

In [19]:
# Combine all reviews text into one list 
all_reviews = "\n".join(stratified_sample["FullText"].tolist())

# Call the function to process the analysis
summary_proscons = generate_proscons_list(all_reviews)

# Print the list of pros and cons (optional step)
print(summary_proscons)

Processing blocks: 100%|██████████| 4/4 [00:10<00:00,  2.74s/block]

Based on the hotel review summaries provided, here are the most common pros and cons for hotel users:

**Pros:**
1. Clean and comfortable rooms with nice views.
2. Friendly and helpful staff.
3. Good facilities for children.
4. Nice pool area.
5. Complimentary tea and cake.
6. Peaceful and scenic location.
7. Free shuttle bus service.
8. Variety of food options for breakfast and lunch.
9. Free WiFi.
10. Lovely lounge area.
11. Free shuttle bus to nearby towns.
12. Great for families with children.
13. Easy access to local attractions.
14. Lovely balcony views.
15. Immaculate cleanliness.
16. Attentive staff.

**Cons:**
1. Not a 4-star hotel standard.
2. Additional charges for amenities like a safe.
3. Lack of tea or coffee making facilities in rooms.
4. Inconsistent quality of food, limited choices.
5. Entertainment and bar facilities could be better.
6. Limited seating at entertainment venues.
7. Inconvenient location for some attractions.
8. Limited variety in the dinner menu.
9. Col

In [20]:
# Summarize the list of pros and cons
messages = [
            {"role": "system", "content": "You are an helpful assistant for text summarization."},
            {"role": "user", "content": f"Based on the list of pros and cons, return the top 10 pros and top 10 cons. Avoid repeating the same topics. Rank the topics based on the numbers of times they appear in the text: {summary_proscons}"}
        ]

completion = openai.chat.completions.create(
    model="gpt-3.5-turbo",
    messages=messages,
    max_tokens=500,
    stop=None,
    temperature=0.7,
    frequency_penalty=0.5,
    top_p=0.5
)

pros_and_cons = completion.choices[0].message.content

print(pros_and_cons)

**Top 10 Pros:**
1. Great location with easy access to the beach and town.
2. Immaculately clean rooms and public areas.
3. Courteous and attentive staff.
4. Beautiful views of the sea and beach.
5. Relaxing pool area with ample sunbeds.
6. Good selection of drinks and food.
7. Spacious rooms with modern amenities.
8. Buffet breakfast with plenty of choices.
9. Quiet and relaxing atmosphere.
10. Convenient parking facilities.

**Top 10 Cons:**
1. Lack of transparency or visibility of hotel management.
2. Delayed room cleaning services.
3. Limited gym facilities.
4. Inconsistent quality of coffee machines at breakfast.
5. Noisy environment due to road traffic or other disturbances.
6. Maintenance issues in rooms or common areas.
7. Lack of storage space in rooms.
8. Inconvenient or additional charges for amenities like safes.
9. Language barriers with staff for non-English speakers.
10. Issues with breakfast area overcrowding and poor customer service.

These top pros and cons are based

### Identifying factors and sentiment

In [21]:
def analyze_review_factors(review, model="gpt-3.5-turbo"):
    """ Get the sentiment per factor """
    retries = 3
    lst = ["POSITIVE", "NEGATIVE", "NEUTRAL"]
    sentiment = {}

    while retries > 0:
        messages = [
            {"role": "system", "content": "You are an AI language model trained to analyze and detect the sentiment of hotel reviews in six factors: Service Quality; Facilities; Value for Money; Rooms; Food and Recreation; Security."},
            {"role": "user", "content": f"Analyze the following hotel review and determine which of the six factors are mentioned in the review and if the sentiment is: positive, negative or neutral. Return a Python dictionary where the key is the factor name and the value is a single word, either POSITIVE, NEGATIVE or NEUTRAL. The Python dictionary should only include keys for the factors found in the text. For Python strings use only single quotes. Text of the review: {review}"}
        ]

        completion = openai.chat.completions.create(
            model=model,
            messages=messages,
            max_tokens=200,
            n=1,
            stop=None,
            temperature=0.5
        )

        response_text = completion.choices[0].message.content
        print(response_text)
        contains_word = lambda s, l: any(map(lambda x: x in s, l))
        if contains_word(response_text,lst):
            sentiment = response_text
            break
        else:
            retries -= 1
            time.sleep(1)
    else:
        sentiment = {}
   
    # add a delay of 4 seconds between requests to avoid hitting the free tier API call rate limit
    time.sleep(4)

    return sentiment

In [22]:
# Analyze the reviews and store the results
factors_sentiments = []

for review in tqdm(stratified_sample["FullText"], desc="Processing reviews"):
    factors_sentiment = analyze_review_factors(review)
    factors_sentiments.append(factors_sentiment)

stratified_sample["Factors_Sentiment"] = factors_sentiments




Processing reviews:   0%|          | 0/50 [00:00<?, ?it/s]

{
    'Service Quality': 'NEGATIVE',
    'Facilities': 'NEGATIVE',
    'Value for Money': 'NEGATIVE',
    'Rooms': 'NEGATIVE',
    'Food and Recreation': 'NEGATIVE'
}


Processing reviews:   2%|▏         | 1/50 [00:04<03:51,  4.72s/it]

{
    'Facilities': 'POSITIVE',
    'Food and Recreation': 'POSITIVE'
}


Processing reviews:   4%|▍         | 2/50 [00:09<03:42,  4.63s/it]

...

Processing reviews:  96%|█████████▌| 48/50 [03:53<00:09,  4.83s/it]

{
    'Service Quality': 'NEUTRAL',
    'Facilities': 'NEGATIVE',
    'Value for Money': 'NEUTRAL',
    'Rooms': 'POSITIVE',
    'Food and Recreation': 'NEUTRAL',
    'Security': 'NEUTRAL'
}


Processing reviews:  98%|█████████▊| 49/50 [03:58<00:04,  4.86s/it]

{
    'Service Quality': 'POSITIVE',
    'Facilities': 'POSITIVE',
    'Rooms': 'POSITIVE',
    'Food and Recreation': 'POSITIVE'
}


Processing reviews: 100%|██████████| 50/50 [04:03<00:00,  4.87s/it]


In [23]:
# Check the text of a review
i=7
print(stratified_sample['FullText'].iloc[i])
print(stratified_sample['Factors_Sentiment'].iloc[i])

Stayed at the Baia Grande with my 5 year old daughter during the May half term holidays. Check-in and out times did not work very well with our flights - but it was easy enough to kill time in the locality. Room was super - lovely bed(s) with everything you needed in the bathroom, large TV, air conditioning and loads of hanging space. The pool area never got particularly busy and the pool itself was beautiful - running from very shallow at one end to cold and deep at the other. Pool bar prices were higher than nearby alternatives, but surely that is to be expected?! We found the staff to be friendly and helpful. The breakfast really did have something for everyone. Sure, the juices and coffee were not the best - but clearly the hotel catering team have a budget to work with! The hotel is not anywhere near Albufeira, but there is enough nearby to ensure you can eat well and keep yourself entertained. The 'Rabbit beach' is only an easy, short walk away. In summary this is a great choice 

In [24]:
# Check the text of a review
i=3
print(stratified_sample['FullText'].iloc[i])
print(stratified_sample['Factors_Sentiment'].iloc[i])

The place was recommended to us a high quality family resort but we were very disappointed by the quality of housing, food and cleanliness overall. <br>The staff was very helpful and friendly which was the best part and helped us find outside activities which made the vacation bearable.
{
    'Service Quality': 'POSITIVE',
    'Facilities': 'NEGATIVE',
    'Rooms': 'NEGATIVE',
    'Food and Recreation': 'NEGATIVE'
}


In [25]:
# Add these factors to the dataset
cleaned_list = [s.replace("\n", "") for s in factors_sentiments]
list_of_dicts = [ast.literal_eval(s) for s in cleaned_list]

# Turn the list of dictionaries into a DataFrame
new_rows_df = pd.DataFrame(list_of_dicts)

# Concatenate the new DataFrame with the existing one, aligning on columns
df = pd.concat([stratified_sample.reset_index(drop=True), new_rows_df], axis=1)


In [26]:
# View the header of the resulting dataframe
df.head()

HotelID Language  GlobalRating  TotalReviewOnSite  ExtractedReviews  \
0        9  English           4.0               3635               535   
1       48  English           4.5               1147               740   
2      100  English           4.5                389                30   
3       23  English           4.5               1925               200   
4       71  English           4.0                757                85   

   PositionInRegionRanking  SitesInRegionRanking  TripadvisorReviewID  \
0                       50                   154            715210414   
1                       10                   154            693473393   
2                       14                   154            692083878   
3                        2                    10            683615537   
4                        2                    14            665491731   

   ReviewRating            PublishedDate  ...  \
0             2  2019-10-01 00:00:00.000  ...   
1             4  2019-07-01 00:00:00.000  ...   
2             5  2019-08-01 00:00:00.000  ...   
3             1  2019-06-01 00:00:00.000  ...   
4             3  2019-04-01 00:00:00.000  ...   

                                            FullText Sentiment  \
0  This is in no way a 4 star hotel ,you have to ...  NEGATIVE   
1  We've just returned from a fab time at this ho...  POSITIVE   
2  A warm welcome awaited us on our arrival and w...  POSITIVE   
3  The place was recommended to us a high quality...  NEGATIVE   
4  We booked this hotel with Jet2 holidays for a ...   NEUTRAL   

                                   Factors_Sentiment Service Quality  \
0  {\n    'Service Quality': 'NEGATIVE',\n    'Fa...        NEGATIVE   
1  {\n    'Facilities': 'POSITIVE',\n    'Food an...             NaN   
2  {\n    'Service Quality': 'POSITIVE',\n    'Fa...        POSITIVE   
3  {\n    'Service Quality': 'POSITIVE',\n    'Fa...        POSITIVE   
4  {\n    'Service Quality': 'POSITIVE',\n    'Fa...        POSITIVE   

  Facilities Value for Money     Rooms Food and Recreation Security Recreation  
0   NEGATIVE        NEGATIVE  NEGATIVE            NEGATIVE      NaN        NaN  
1   POSITIVE             NaN       NaN            POSITIVE      NaN        NaN  
2   POSITIVE         NEUTRAL  POSITIVE            POSITIVE  NEUTRAL        NaN  
3   NEGATIVE             NaN  NEGATIVE            NEGATIVE      NaN        NaN  
4    NEUTRAL             NaN   NEUTRAL             NEUTRAL      NaN        NaN  

[5 rows x 23 columns]

### Moderation
Check if reviews contain violence, hate, or discrimination

In [27]:
def analyze_review_moderation(review):
    """ Moderate review """
    
    output = None
    
    response = openai.moderations.create(input = review)

    output = response.results[0]
   
    # add a delay of 4 seconds between requests to avoid hitting the free tier API call rate limit
    time.sleep(4)

    return output

In [28]:
# Analyze the reviews and store the results
moderation_output = []

for review in tqdm(stratified_sample["FullText"], desc="Processing reviews"):
    moderation = analyze_review_moderation(review)
    moderation_output.append(moderation)

Processing reviews: 100%|██████████| 50/50 [04:04<00:00,  4.89s/it]


In [29]:
# Check the overall result of the first review
moderation_output[0]

Moderation(categories=Categories(harassment=False, harassment_threatening=False, hate=False, hate_threatening=False, illicit=None, illicit_violent=None, self_harm=False, self_harm_instructions=False, self_harm_intent=False, sexual=False, sexual_minors=False, violence=False, violence_graphic=False, self-harm=False, sexual/minors=False, hate/threatening=False, violence/graphic=False, self-harm/intent=False, self-harm/instructions=False, harassment/threatening=False), category_applied_input_types=None, category_scores=CategoryScores(harassment=0.026297861710190773, harassment_threatening=0.0001697603438515216, hate=0.00417799036949873, hate_threatening=2.3985580810403917e-06, illicit=None, illicit_violent=None, self_harm=1.801067810447421e-06, self_harm_instructions=1.2977936421521008e-05, self_harm_intent=7.901753633632325e-07, sexual=4.79954587717657e-06, sexual_minors=1.4816654356764047e-06, violence=0.00017603016749490052, violence_graphic=0.0001223611325258389, self-harm=1.8010678104

In [30]:
# Checking the full output of the first review
moderation_output[0].flagged

False

## References

- How to get around OpenAI GPT token limits: https://blog.devgenius.io/how-to-get-around-openai-gpt-3-token-limits-b11583691b32
- How Transformers work: https://towardsdatascience.com/illustrated-guide-to-transformers-step-by-step-explanation-f74876522bc0
- Examples of reviews analysis: https://blog.startupstash.com/analyze-customer-product-reviews-using-chatgpt-openai-api-a-step-by-step-guide-to-extracting-5cb599608c8d#829f-1370f316f4aa and https://medium.com/data-and-beyond/sentiment-analysis-with-chatgpt-openai-and-python-use-chatgpt-to-build-a-sentiment-analysis-ai-2b89158a37f6
- Topic modeling using Bertopic: https://towardsdatascience.com/topic-modelling-using-chatgpt-api-8775b0891d16



